# 파이썬 X 스타벅스 매장 데이터와 지도

<img src="https://i.imgur.com/ik6NVEo.png" >

* requests 위치 데이터 가져오기
* json_normalize(): JSON 데이터 DataFrame으로 전환
* folium 을 사용하여 지도에 위치 표시

<!-- TEASER_END -->

### 2018 FinanceData.KR [fb.com/financedata](fb.com/financedata)

# 스타벅스 + 부동산 투자?
* https://goo.gl/PEhtz7  스타벅스, 벅세권
* https://goo.gl/TIM2Mw 부동산 시장까지 사로잡은 스타벅스

<img width="60%" src="https://i.imgur.com/VwQhySO.jpg" >

# 스타벅스 매장찾기
http://www.istarbucks.co.kr

* STORE >> 매장 찾기
* 지역검색 >> 서울 >> 전체

In [1]:
import requests
import json
import pandas as pd
from pandas.io.json import json_normalize

In [2]:
data = {
    'ins_lat':'37.56682', # 지정한 위도와 경도에서 가까운 순으로 나열
    'ins_lng':'126.97865',
    'p_sido_cd':'01', # 01=서울시, 08=경기 ... 16=제주
    'p_gugun_cd':'',  # 세부지역 (지정하지 않으면 시/도 전체)
    'in_biz_cd':'',
    'set_date':'',
    'iend':'1000',
}
    
url = 'https://www.istarbucks.co.kr/store/getStore.do'
r = requests.post(url, data=data)

r.text[:1000] # 수신된 데이터의 앞부분만 확인

'{"list":[{"seq":0,"sido_cd":null,"sido_nm":null,"gugun_cd":null,"gugun_nm":null,"code_order":null,"view_yn":null,"store_num":null,"sido":null,"gugun":null,"address":null,"new_img_nm":null,"p_pro_seq":0,"p_view_yn":null,"p_sido_cd":"","p_gugun_cd":"","p_store_nm":null,"p_theme_cd":null,"p_wireless_yn":null,"p_smoking_yn":null,"p_book_yn":null,"p_music_yn":null,"p_terrace_yn":null,"p_table_yn":null,"p_takeout_yn":null,"p_parking_yn":null,"p_dollar_assent":null,"p_card_recharge":null,"p_subway_yn":null,"stb_store_file_renew":null,"stb_store_theme_renew":null,"stb_store_time_renew":null,"stb_store_lsm":null,"s_code":"1047","s_name":"한국프레스센터","tel":"02-722-3263","fax":"02-722-3264","sido_code":"01","sido_name":"서울","gugun_code":"0119","gugun_name":"중구","addr":"서울특별시 중구 태평로1가 25 프레스센터","park_info":null,"new_state":null,"theme_state":"T17@P80@T08@T09@T05@T20@T16@T07@T04","new_bool":0,"search_text":"","ins_lat":"","ins_lng":"","in_distance":0,"out_distance":".09","all_search_cnt":-1,"addr_sea

데이터는 JSON으로 수신되며, 형태는 다음과 같다.

```json
{
  "list": [
      {
            // ... 중략 ...
            "s_code": "1311",
            "s_name": "방화DT",
            "tel": "02-2664-3480",
            "fax": "02-2664-3481",
            "sido_code": "01",
            "sido_name": "서울",
            "gugun_code": "0103",
            "gugun_name": "강서구",
            "addr": "서울특별시 강서구 방화동 293-4",
            "park_info": null,
            "new_state": null,
            "theme_state": "T17@T16@T09@T20@T01@T05@T08@T04",
            // ... 중략 ...
            "lat": "37.574339",
            "lot": "126.816415",
            "t22": 0
        },
        {
            // ... 중략 ...
            "s_code": "1267",
            "s_name": "마곡나루역",
            "tel": "02-3662-3504",
            "fax": "02-3662-3505",
            "sido_code": "01",
            "sido_name": "서울",
            "gugun_code": "0103",
            "gugun_name": "강서구",
            "addr": "서울특별시 강서구 마곡동 759-3 보타닉파크타워Ⅰ105,203,204호",
            "park_info": null,
            "new_state": null,
            "theme_state": "T08@T05@T04@T17@T16@P80@T20",
            // ... 중략 ...
            "lat": "37.56813",
            "lot": "126.82614",
            "t22": 0
        },
    ]
 }
```

# JSON to DataFrame

json_normalize() 를 사용하여 JSON 데이터를 DataFrame로 전환 

In [3]:
jo = json.loads(r.text)
df = json_normalize(jo, 'list')

In [4]:
# 행(row)수, 서울 457개 매장
len(df) 

457

In [5]:
# 컬럼수 111개
df.columns

Index(['addr', 'addr_search_cnt', 'address', 'all_search_cnt', 'code_order',
       'cold_blew', 'defaultimage', 'disp', 'doro_address', 'espresso',
       ...
       't06', 't09', 't10', 't12', 't20', 't22', 'tel', 'theme_state', 'vSal',
       'view_yn'],
      dtype='object', length=111)

In [6]:
# 주요한 컬럼 몇 가지 선택
               
df = df[['s_name', 'lat', 'lot', 'sido_name', 'gugun_name', 'doro_address', 'tel']]
df.head(20)

s_name          lat                 lot sido_name gugun_name  \
0    한국프레스센터    37.567381          126.977859        서울         중구   
1        무교동  37.56781712          126.978738        서울         중구   
2         시청    37.566290          126.979808        서울         중구   
3      시청플러스    37.566338          126.980055        서울         중구   
4        소공동    37.564448          126.979157        서울         중구   
5    을지로국제빌딩    37.566952          126.982219        서울         중구   
6      소공로북창   37.5636856         126.9789237        서울         중구   
7        소공로   37.5637273  126.98076809999998        서울         중구   
8    을지로경기빌딩    37.567172          126.983156        서울         중구   
9       영풍문고   37.5695584         126.9821243        서울        종로구   
10   을지로한국빌딩    37.565722           126.98329        서울         중구   
11  을지로내외빌딩R    37.566479          126.983663        서울         중구   
12      새문안로   37.5696597         126.9748903        서울        종로구   
13       서소문   37.5633773  126.97551290000001        서울         중구   
14     명동메트로    37.565118          126.983681        서울         중구   
15      명동입구    37.563319          126.982242        서울         중구   
16    광화문D타워      37.5714         126.9788297        서울        종로구   
17       태평로  37.56248285         126.9767928        서울         중구   
18      광화문R   37.5712293         126.9762872        서울        종로구   
19   을지로삼화타워    37.566902          126.984707        서울         중구   

                              doro_address          tel  
0                서울특별시 중구 세종대로 124 (태평로1가)  02-722-3263  
1           서울특별시 중구 무교로 21 (무교동) 코오롱빌딩 1층  02-758-8037  
2     서울특별시 중구 을지로 19, 삼성화재삼성빌딩 1층 (을지로1가)  02-758-8504  
3     서울특별시 중구 을지로 19, 삼성화재삼성빌딩 1층 (을지로1가)  02-758-8505  
4                   서울특별시 중구 소공로 112 (소공동)  02-758-8140  
5                   서울특별시 중구 남대문로 109 (다동)  02-752-3464  
6           서울특별시 중구 세종대로18길 32 (소공동) 삼원빌딩  02-758-8843  
7     서울특별시 중구 남대문로7길 19, 삼영빌딩 1층 일부 (소공동)  02-758-8569  
8            서울특별시 중구 남대문로10길 9 (삼각동) 경기빌딩  02-758-8981  
9             서울특별시 종로구 청계천로 41 (서린동) 영풍빌딩  02-758-8083  
10            서울특별시 중구 을지로 50, 1층 (을지로 2가)  02-758-8385  
11                 서울특별시 중구 을지로 51 (을지로2가)  02-754-3429  
12     서울특별시 종로구 새문안로 92 (신문로1가) 광화문오피시아빌딩  02-758-8788  
13                서울특별시 중구 서소문로 130 (서소문동)  02-758-8181  
14         서울특별시 중구 명동9가길 14 (을지로1가) 메트로호텔  02-758-8764  
15               서울특별시 중구 남대문로 68-1 (명동2가)  02-758-8506  
16             서울특별시 종로구 종로3길 17 (청진동) D타워  02-758-8954  
17       서울특별시 중구 세종대로 72, 대영빌딩 1층 (태평로2가)  02-758-8039  
18  서울특별시 종로구 세종대로 167, 현대해상본사사옥 별관내 (세종로)  02-758-8036  
19                서울특별시 중구 을지로5길 16 삼화타워1층  02-758-8483

# 위도 경도 데이터 타입 변환

In [7]:
df.dtypes

s_name          object
lat             object
lot             object
sido_name       object
gugun_name      object
doro_address    object
tel             object
dtype: object

### lat, lot타입으로 전환 (str→float) 

In [8]:
df['lat'] = df['lat'].astype(float)
df['lot'] = df['lot'].astype(float)

In [9]:
df.dtypes

s_name           object
lat             float64
lot             float64
sido_name        object
gugun_name       object
doro_address     object
tel              object
dtype: object

### 특정 지점

In [10]:
df[df['s_name'] == '시청'] # 시청점

s_name       lat         lot sido_name gugun_name  \
2     시청  37.56629  126.979808        서울         중구   

                           doro_address          tel  
2  서울특별시 중구 을지로 19, 삼성화재삼성빌딩 1층 (을지로1가)  02-758-8504

스타벅스 시청점의 위도(lat)와 경도(lot)는 각각  37.56629, 126.979808

# folium
https://github.com/python-visualization/folium

파이썬 지리정보 시각화 모듈  (문서: https://folium.readthedocs.io )

In [11]:
import folium

# 서울 시청 
map_osm = folium.Map(location=(37.56629, 126.979808))
map_osm

지도를 상하좌우로 움직이거나 확대/축소 할 수 있다

In [12]:
# 확대 지정 (zoom_start)
map_osm = folium.Map(location=(37.56629, 126.979808), zoom_start=17)
map_osm

In [13]:
# 지도 tiles 지정
map_osm = folium.Map(location=(37.56629, 126.979808), zoom_start=17, tiles='Stamen Toner')
map_osm

In [14]:
시청_좌표=(37.56629, 126.979808)
 
map_osm = folium.Map(location=시청_좌표, zoom_start=17)
folium.Marker(시청_좌표, popup='시청').add_to(map_osm)
map_osm

# 서울 스타벅스 전 지점

In [15]:
map_osm = folium.Map(location=시청_좌표, zoom_start=11)

for ix, row in df.iterrows():
    location = (row['lat'], row['lot'])
    folium.Marker(location, popup=row['s_name']).add_to(map_osm)

map_osm

# 제주도 스타벅스 매장 지도

In [16]:
import requests
import json
import pandas as pd
from pandas.io.json import json_normalize

한라산_좌표 = (33.361666, 126.529166)

data = {
    'ins_lat': '33.4996213', # 제주 시청의 좌표
    'ins_lng': '126.5311884',
    'p_sido_cd':'16', # 01=서울시, 08=경기 ... 16=제주
    'p_gugun_cd':'',  # 세부지역 (지정하지 않으면 시/도 전체)
    'in_biz_cd':'',
    'set_date':'',
    'iend':'1000',
}
    
url = 'https://www.istarbucks.co.kr/store/getStore.do'
r = requests.post(url, data=data)
df = json_normalize(json.loads(r.text), 'list')

map_osm = folium.Map(location=한라산_좌표, zoom_start=10)
for ix, row in df.iterrows():
    location = (row['lat'], row['lot'])
    folium.Marker(location, popup=row['s_name']).add_to(map_osm)

map_osm

In [17]:
df[['s_name', 'gugun_name', 'doro_address', 'tel']]

s_name gugun_name                             doro_address           tel
0      제주칠성        제주시                제주특별자치도 제주시 관덕로 55 (일도일동)  064-757-9892
1       신제주        제주시                  제주특별자치도 제주시 노연로 99 (연동)  064-747-8472
2    제주용담DT        제주시       제주특별자치도 제주시 서해안로 380 (용담삼동) 화이트하우스  064-745-9817
3      제주노형        제주시                 제주특별자치도 제주시 도령로 27 (노형동)  064-745-8914
4    제주노형공원        제주시                 제주특별자치도 제주시 연북로 12 (노형동)  064-746-3367
5    신제주이마트        제주시  제주특별자치도 제주시 1100로 3348, 신제주이마트 1층 (노형동)  064-748-8657
6    제주애월DT        제주시               제주특별자치도 제주시 애월읍 애월해안로 376   064-799-3273
7     서귀포DT       서귀포시               제주특별자치도 서귀포시 일주서로 11 (강정동)  064-738-5943
8     제주서귀포       서귀포시                제주특별자치도 서귀포시 중정로 53 (서귀동)  064-763-8707
9    제주중문DT       서귀포시                제주특별자치도 서귀포시 천제연로 95(색달동)  064-738-8915
10  제주신화월드R       서귀포시     제주특별자치도 서귀포시 안덕면 신화역사로304번길 38 B1-29  064-908-1729
11     제주중문       서귀포시         제주특별자치도 서귀포시 중문관광로110번길 32 (색달동)  064-738-8510
12   제주에듀시티       서귀포시               제주특별자치도 서귀포시 대정읍 에듀시티로 36   064-792-3371
13   제주성산DT       서귀포시                 제주특별자치도 서귀포시 성산읍 일출로 80   064-782-3273
14    성산일출봉       서귀포시         제주특별자치도 서귀포시 성산읍 일출로 284-5, 1,2층  064-782-8535
15    제주송악산       서귀포시             제주특별자치도 서귀포시 형제해안로 322 (상모리)  064-792-8731

# 요약
* requests.post() 데이터 가져오기
* json_normalize(): JSON 데이터 DataFrame으로 전환
* folium 을 사용하여 지도에 위치 표시

### 2018 FinanceData.KR [fb.com/financedata](fb.com/financedata)